In [1]:
%matplotlib inline

In [57]:
import numpy as np
import matplotlib.pyplot as plt
import librosa as lb
import IPython.display as ipd
from scipy.signal import medfilt
import scipy.io as sio
import math
import pyaudio
import wave
import ipywidgets as widgets
import soundfile as sf
import io
import audioop
import time

### Implement TSM with dynamically changing time stretch factor in an offline setting 
In hw10 we implemented the following function
y = tsm_hybrid(x, alpha=1.0, sr=22050)
Where x is the input audio, y is the output audio, alpha is the global TSM factor, and sr is the sample rate
* You will implement the following function
y = tsm_hybrid_variable(x, sr, t_alpha, alpha)
x, sr, and y are same as above
alpha is a 1-d array specifying the desired TSM factors at different points in time
t_alpha is a 1-d array of the same size as alpha that specifies the time (in sec, in the timeline of the original unmodified audio recording) when the TSM factor should be changed/set; the first value of this array should always be zero (in order to set the initial TSM factor)
* You can think of t_alpha and alpha as a way of simulating a  person controlling the slider where they make a discrete number of changes over the length of the recording
E.g. if t_alpha = [0,2.5, 7.5] and alpha = [1.0, 2.0, 0.5], then the first 2.5 sec of the original audio should be played with no TSM, the next 7.5 - 2.5 = 5 sec of the original audio should be played with time stretch factor 2x, and the rest of the recording should be played with time stretch factor 0.5.

Use a simple example like this to verify that your code is working properly – you should be able to double check that the total duration is what is expected, and also listen to confirm that it is doing the time stretch properly


#### Helper functions

In [3]:
def invert_stft(S, hop_length, window):
    '''
    Reconstruct a signal from a modified STFT matrix.
    
    Inputs
    S: modified STFT matrix
    hop_length: the synthesis hop size in samples
    window: an array specifying the window used for FFT analysis
    
    Returns a time-domain signal y whose STFT is closest to S in squared error distance.
    '''
    
    L = len(window)
    
    # construct full stft matrix
    fft_size = (S.shape[0] - 1) * 2
    Sfull = np.zeros((fft_size, S.shape[1]), dtype=np.complex64)
    Sfull[0:S.shape[0],:] = S
    Sfull[S.shape[0]:,:] = np.conj(np.flipud(S[1:fft_size//2,:]))
    
    # compute inverse FFTs
    frames = np.zeros_like(Sfull)
    for i in range(frames.shape[1]):
        frames[:,i] = np.fft.ifft(Sfull[:,i])
    frames = np.real(frames) # remove imaginary components due to numerical roundoff
    
    # synthesis frames
    num = window.reshape((-1,1))
    den = calc_sum_squared_window(window, hop_length)
    #den = np.square(window) + np.square(np.roll(window, hop_length))
    frames = frames * window.reshape((-1,1)) / den.reshape((-1,1))
    #frames = frames * window.reshape((-1,1))
    
    # reconstruction
    y = np.zeros(hop_length*(frames.shape[1]-1) + L)
    for i in range(frames.shape[1]):
        offset = i * hop_length
        y[offset:offset+L] += frames[:,i]
    
    return y

In [4]:
def calc_sum_squared_window(window, hop_length):
    '''
    Calculates the denominator term for computing synthesis frames.
    
    Inputs
    window: array specifying the window used in FFT analysis
    hop_length: the synthesis hop size in samples
    
    Returns an array specifying the normalization factor.
    '''
    assert (len(window) % hop_length == 0), "Hop length does not divide the window evenly."
    
    numShifts = len(window) // hop_length
    den = np.zeros_like(window)
    for i in range(numShifts):
        den += np.roll(np.square(window), i*hop_length)
        
    return den

In [5]:
def harmonic_percussive_separation(x, sr=22050, fft_size = 2048, hop_length=512, lh=6, lp=6):
    
    window = np.hanning(fft_size)
    X = lb.core.stft(x, n_fft=fft_size, hop_length=512, window=window, center=False)
    Y = np.abs(X)
    Yh = medfilt(Y, (1, 2*lh+1))
    Yp = medfilt(Y, (2*lp+1, 1))
    Mh = (Yh > Yp)
    Mp = np.logical_not(Mh)
    Xh = X * Mh
    Xp = X * Mp
    xh = invert_stft(Xh, hop_length, window)
    xp = invert_stft(Xp, hop_length, window)
    
    return xh, xp, Xh, Xp

In [6]:
def mix_recordings(x1, x2):
    min_length = min(len(x1), len(x2))
    y = .5 * (x1[0:min_length] + x2[0:min_length])
    return y

### Including dynamic variable

#### tsm_ola_variable, applying OLA when we have a dynamic variable $\alpha$

In [7]:
choir, c_sr = lb.load("choir.wav")
beatbox, bb_sr = lb.load("beatbox.wav")

In [8]:
def tsm_ola_variable(x, sr, t_alpha, alpha, L=220):
    '''
    Time stretches the input signal using overlap-add with variable stretch factors.
    
    Inputs:
    x: input signal
    sr: sample rate
    t_alpha: array of time points (seconds) when stretch factors change
    alpha: array of stretch factors corresponding to t_alpha
    L: frame length (must be even)
    
    Returns time-stretched signal y
    '''
    assert L % 2 == 0, "Frame length must be even."
    Hs = L // 2
    
    # Convert time points to samples
    t_alpha_samples = [int(t * sr) for t in t_alpha]
    t_alpha_samples.append(len(x))  # Add end of signal as final boundary
    
    # Initialize
    current_alpha_idx = 0
    curr_offset = 0
    analysis_frames = []
        
    # Analysis phase
    while curr_offset <= len(x) - L:
        current_alpha = alpha[current_alpha_idx]
        Ha = int(np.round(Hs / current_alpha))

        # Check if next window would cross boundary
        if curr_offset + Ha > t_alpha_samples[current_alpha_idx + 1]:
            current_alpha_idx += 1
        
        # Extract and store frame
        frame = x[curr_offset:curr_offset + L]
        analysis_frames.append(frame)        
        # Advance position
        curr_offset += Ha
    
    num_frames = len(analysis_frames)
    if num_frames == 0:
        return np.zeros(0)
    
    analysis_frames = np.array(analysis_frames).T
    
    # Synthesis phase
    synthesis_frames = analysis_frames * hann_window(L).reshape((-1, 1))
    y = np.zeros(Hs * (num_frames-1) + L)
    
    for i in range(num_frames):
        offset = i * Hs
        y[offset:offset + L] += synthesis_frames[:, i]
    
    return y

In [9]:
def hann_window(L):
    w = .5 * (1 - np.cos(2*np.pi * np.arange(L)/ L))
    return w

In [10]:
t_alpha = [0]
alpha = [0.75]
beatbox_ola = tsm_ola_variable(beatbox, bb_sr, t_alpha, alpha)
choir_ola = tsm_ola_variable(choir, c_sr, t_alpha, alpha)

In [11]:
ipd.Audio(beatbox_ola, rate=bb_sr)

In [12]:
ipd.Audio(choir_ola, rate=c_sr)

#### tsm_phase_vocoder_variable, applying phase vocoder when we have a dynamic variable $\alpha$

In [13]:
def tsm_phasevocoder_variable(x, sr, t_alpha, alpha, L=2048):
    """
    Phase‐vocoder time‐scale modification with piecewise constant speed factors.
    
    Parameters
    ----------
    x : np.ndarray
        Input audio signal (1D array of samples).
    sr : int
        Sampling rate in Hz.
    t_alpha : list of float
    alpha : list of float
        Speed factors corresponding to each segment defined by `t_alpha`.
    L : int, optional
        FFT size and window length (defaults to 2048 samples).
    
    Returns
    -------
    y : np.ndarray
        Time‐scaled output signal.
    """
    Hs = L // 4
    window = np.hanning(L)  # Hann window of length L

    t_alpha_samples = [int(t * sr) for t in t_alpha] + [len(x)]
    prev_fft = None # stores the FFT of the previous frame (None for first frame)
    prev_phase = np.zeros(L//2 + 1) # half of the size of FFT
    currOffset = 0 # current read pointer in the input x
    seg_idx = 0 # which segment (alpha[seg_idx]) we’re in
    analysisFrames = []

    # precompute nominal angular frequencies for each FFT bin
    omega_nom = np.arange(L//2 + 1) * 2 * np.pi * sr / L

    # main processing loop
    while currOffset + L <= len(x): # stop when not enough frame for entire window
        if currOffset >= t_alpha_samples[seg_idx + 1]:
            seg_idx += 1 # if we’ve crossed the next time boundary, increment seg_idx.
        a  = alpha[seg_idx] #the speed factor for this frame.
        Ha = int(round(Hs / a)) # Ha length in terms of Hs --> output_length approx input_length * (Ha / Hs)

        # extract, window, and FFT the current frame
        frame = x[currOffset : currOffset + L] * window
        S     = np.fft.rfft(frame)

    # estimate IF
        if prev_fft is None: # nothing for first frame
            w_if = np.zeros_like(omega_nom)
        else:
            
            dphi = np.angle(S) - np.angle(prev_fft) # phase difference between current & previous FFT
            dphi = dphi - omega_nom * (Ha / sr)
            
            dphi = (dphi + np.pi) % (2 * np.pi) - np.pi # wrap to [-π, π] to undo any 2π jumps
            w_if = omega_nom + dphi * (sr / Ha) # IF = nom + correction
 
        prev_phase = prev_phase + w_if * (Hs / sr) # accumulates phase after every time boundary

        # build the modified spectrum & inverse FFT back to time domain
        X_mod = np.abs(S) * np.exp(1j * prev_phase)
        frame_mod = np.fft.irfft(X_mod)
        analysisFrames.append(frame_mod)

        # advance pos
        currOffset  += Ha
        prev_fft   = S

    numFrames = len(analysisFrames)
    analysisFrames = np.array(analysisFrames).T
    den = calc_sum_squared_window(window, Hs)
    synthesisFrames = analysisFrames * window.reshape((-1,1)) / den.reshape((-1,1))
    y = np.zeros((Hs*numFrames)+L)

    for i in range(numFrames):
        offset = i * Hs
        y[offset: offset + L] += synthesisFrames[:, i]

    return y


In [14]:
t_alpha = [0, 2.5, 7.5]
alpha = [1, 2, 0.5]

In [58]:
choirVocoderStart = time.perf_counter()

choir_vocoder = tsm_phasevocoder_variable(choir, c_sr, t_alpha, alpha)

choirVocoderEnd = time.perf_counter()

choirVocoderTime = choirVocoderEnd - choirVocoderStart

print(f"Runtime: {choirVocoderTime}")



Runtime: 0.10125009994953871


In [59]:
BBVocoderStart = time.perf_counter()


beatbox_vocoder = tsm_phasevocoder_variable(beatbox, bb_sr, t_alpha, alpha)


BBVocoderEnd = time.perf_counter()

BBVocoderTime = BBVocoderEnd - BBVocoderStart

print(f"Runtime: {BBVocoderTime}")

Runtime: 0.1256669000722468


In [55]:
ipd.Audio(choir_vocoder, rate=c_sr)

In [56]:
ipd.Audio(beatbox_vocoder, rate=bb_sr)

### optimizing PV function

In [18]:
def precompute_stft_frames(x, L=2048, Ha_base=2048//512):
    if Ha_base is None:
        Ha_base = L // 8    # instead of L//4, choose L//8 or even L//16
    window = np.hanning(L).astype(np.float32)
    frames = []
    for start in range(0, len(x) - L + 1, Ha_base):
        frame = x[start:start + L] * window
        S = np.fft.rfft(frame)
        frames.append(S)
    return np.array(frames), window, Ha_base


In [19]:
def tsm_phasevocoder_precomputed(x, sr, STFT, window, t_alpha, alpha, L=2048, Hs=512, Ha_base=2048//512):
    """
    Phase vocoder time-scale modification using a precomputed STFT bank.
    Includes linear interpolation between FFT frames to improve smoothness.
    """

    # Convert segment time boundaries from seconds to sample indices
    # t_alpha defines when alpha (speed factor) changes; we add len(x) as the final boundary
    t_alpha_samps = [int(t * sr) for t in t_alpha] + [len(x)]

    # Get number of FFT frames and frequency bins from the precomputed STFT
    n_frames, n_bins = STFT.shape

    # Precompute the nominal angular frequencies (omega) for each FFT bin
    omega_nom = np.arange(n_bins) * 2 * np.pi * sr / L

    # Variables for tracking previous frame and output phase
    prev_fft = None
    prev_phase = np.zeros(n_bins, dtype=np.float32)  # initialized to 0 phase
    y_frames = []  # list to hold processed output frames
    curr_t = 0.0   # "virtual" read position in input (can be fractional)
    seg_idx = 0    # index of current alpha segment

    # Main time-scaling loop
    while True:
        # If we're past the end of the current time segment, move to the next
        if seg_idx < len(alpha) - 1 and curr_t >= t_alpha_samps[seg_idx + 1]:
            seg_idx += 1

        # Get the current speed factor
        a = alpha[seg_idx]

        # Compute how far ahead to jump in the input STFT (in samples)
        Ha = Hs / a                    # analysis hop size (smaller for slow-down, larger for speed-up)
        next_t = curr_t + Ha          # virtual read pointer advances by Ha

        # Find the fractional index into the precomputed STFT array
        fpos = next_t / Ha_base       # fractional frame index in STFT
        i0 = int(np.floor(fpos))      # lower index
        w = fpos - i0                 # interpolation weight (between 0 and 1)
        i1 = i0 + 1                   # upper index

        # If we’ve reached the end of the STFT bank, we’re done
        if i1 >= n_frames:
            break

        # Retrieve the two FFT frames for interpolation
        S0 = STFT[i0]
        S1 = STFT[i1]

        # INTERPOLATE MAGNITUDE
        # Linearly blend magnitudes of neighboring STFT frames
        mag0 = np.abs(S0)
        mag1 = np.abs(S1)
        mag = (1 - w) * mag0 + w * mag1

        # INTERPOLATE PHASE
        # Extract phases from both STFT frames
        ph0 = np.angle(S0)
        ph1 = np.angle(S1)

        # Compute shortest angular difference between phases
        dph = (ph1 - ph0 + np.pi) % (2 * np.pi) - np.pi

        # Linearly interpolate unwrapped phase difference
        ph = ph0 + w * dph

        # Construct the interpolated FFT with new magnitude and phase
        S = mag * np.exp(1j * ph)

        # INSTANTANEOUS FREQUENCY ESTIMATION
        if prev_fft is None:
            # First frame: no IF estimate, use zero
            w_if = np.zeros_like(omega_nom)
        else:
            # Estimate phase advance from previous to current frame
            dphi = np.angle(S) - np.angle(prev_fft)
            dphi -= omega_nom * (Ha / sr)       # remove expected phase advance
            dphi = (dphi + np.pi) % (2 * np.pi) - np.pi  # wrap to [-π, π]
            w_if = omega_nom + dphi * (sr / Ha) # true instantaneous frequency

        # PHASE ACCUMULATION
        # Update running phase accumulator to generate coherent output
        prev_phase = prev_phase + w_if * (Hs / sr)

        # INVERSE FFT BACK TO TIME DOMAIN
        # Use updated phase and interpolated magnitude
        X_mod = mag * np.exp(1j * prev_phase)
        frame_mod = np.fft.irfft(X_mod)          # convert to time domain
        y_frames.append(frame_mod)               # store frame for overlap-add

        # Update previous FFT and advance read pointer
        prev_fft = S
        curr_t = next_t

    # OVERLAP-ADD SYNTHESIS
    # Transpose from list of frames to matrix: each column = one frame
    analysis_frames = np.array(y_frames).T

    # Calculate normalization factor from window function
    den = calc_sum_squared_window(window, Hs)

    # Apply window and normalize each frame
    synthesis = analysis_frames * window.reshape(-1, 1) / den.reshape(-1, 1)

    # Initialize output buffer large enough to hold all frames
    y_len = int(Hs * len(y_frames)) + L
    y = np.zeros(y_len, dtype=np.float32)

    # Overlap-add all frames into final output
    for i, frame in enumerate(synthesis.T):
        start = int(i * Hs)
        y[start:start + L] += frame

    return y  # return the synthesized, time-scaled signal

In [20]:
# def precompute_stft_frames(x, L=2048, Ha_base=2048//512):
# def tsm_phasevocoder_precomputed(x, sr, STFT, window, t_alpha, alpha, L=2048, Hs=512, Ha_base=2048//512):
t_alpha = [0, 2.5, 7.5]
alpha = [1.25, 1.0, 0.75]

choirPrecomputed, choirWindow, choirHa_base = precompute_stft_frames(choir)

beatboxPrecomputed, bbWindow, bbHa_base = precompute_stft_frames(beatbox)

In [ ]:
# import time

# start_time = time.perf_counter()

# # Code to be timed
# for i in range(100000):
#     _ = i * i

# end_time = time.perf_counter()

# execution_time = end_time - start_time
# print(f"Execution time: {execution_time:.4f} seconds")

In [ ]:
pStartChoir = time.perf_counter()

yChoirPre = tsm_phasevocoder_precomputed(choir, c_sr, choirPrecomputed, choirWindow, t_alpha, alpha) ###

pEndChoir = time.perf_counter()

pChoirRuntime = pEndChoir - pStartChoir

print(f"Runtime: {pChoirRuntime}")



Runtime: 0.16122899996116757


In [52]:
pStartBB = time.perf_counter()

yBBPre = tsm_phasevocoder_precomputed(beatbox, bb_sr, beatboxPrecomputed, bbWindow, t_alpha, alpha) ###

pEndBB = time.perf_counter()

pBBRuntime = pEndBB - pStartBB

print(f"Runtime: {pBBRuntime}")

Runtime: 0.1651890000794083


In [22]:
ipd.Audio(yChoirPre, rate=c_sr)

In [23]:
ipd.Audio(yBBPre, rate=bb_sr)

#### tsm_hybrid_variable, applying hybrid method when we have a dynamic variable $\alpha$

In [24]:
def tsm_hybrid_variable(x, sr, alpha, t_alpha):
    """
    Inputs:
    x - input signal
    sr - sampling rate
    alpha - a list of stretch factos
    t_alpha - a list of times (in seconds) where the stretch factor, alpha, applies e.g. alpha = [1, 0.5, 2] and t_alpha = [0, 2.5, 6]
    then from 0 to 2.5 secs, alpha = 1, then from 2.5 to 6 secs, alpha = 0.5 and so on. 
    """
    xh, xp, _, _ = harmonic_percussive_separation(x)
    xh_stretched = tsm_phasevocoder_variable(xh, sr, t_alpha, alpha)
    xp_stretched = tsm_ola_variable(xp, sr, t_alpha, alpha)
    y = mix_recordings(xh_stretched, xp_stretched)
    return y

In [25]:
t_alpha = [0, 2.5, 6]
alpha = [1, 1.25, 0.75]

In [26]:
beatbox_y = tsm_hybrid_variable(beatbox, bb_sr, alpha, t_alpha)

In [27]:
choir_y = tsm_hybrid_variable(choir, c_sr, alpha, t_alpha)

In [28]:
ipd.Audio(beatbox_y, rate=bb_sr)

In [29]:
ipd.Audio(choir_y, rate=c_sr)

### Faster ver. of Hybrid method

In [30]:
# Preprocessing step (done once before user interaction)

# def precompute_stft_frames(x, L=2048, Ha_base=2048//512):
# def tsm_phasevocoder_precomputed(x, sr, STFT, window, t_alpha, alpha, L=2048, Hs=512, Ha_base=2048//512):
Choirxh, Choirxp, _, _ = harmonic_percussive_separation(choir, sr=c_sr)

beatboxxh, beatboxxp, _, _ = harmonic_percussive_separation(beatbox, sr=bb_sr)



In [31]:
def tsm_hybrid_variable_optimized(xh, xp, sr, alpha, t_alpha, precomputed, window):
    """
    Inputs:
    x - input signal
    sr - sampling rate
    alpha - a list of stretch factos
    t_alpha - a list of times (in seconds) where the stretch factor, alpha, applies e.g. alpha = [1, 0.5, 2] and t_alpha = [0, 2.5, 6]
    then from 0 to 2.5 secs, alpha = 1, then from 2.5 to 6 secs, alpha = 0.5 and so on. 
    """
    
    xh_stretched = tsm_phasevocoder_precomputed(xh, sr, precomputed, window, t_alpha, alpha)
    xp_stretched = tsm_ola_variable(xp, sr, t_alpha, alpha)
    y = mix_recordings(xh_stretched, xp_stretched)
    return y

In [32]:
t_alpha = [0, 2.5, 6]
alpha = [1, 1.25, 0.75]

In [33]:
beatbox_yopt = tsm_hybrid_variable_optimized(beatboxxh, beatboxxp, bb_sr, alpha, t_alpha, beatboxPrecomputed, bbWindow)

In [34]:
ipd.Audio(beatbox_yopt, rate=bb_sr)

In [35]:
choir_yopt = tsm_hybrid_variable_optimized(Choirxh, Choirxp, c_sr, alpha, t_alpha, choirPrecomputed, choirWindow)

In [36]:
ipd.Audio(choir_yopt, rate=bb_sr)

### Implement TSM with simulated real-time processing with a single global time stretch factor

You will want to keep track of where you are in the original audio recording (i.e. the sample offset where you are currently located), this will form the outer loop of the algorithm:
 - Figure out what data needs to be accessed in order to compute the next chunk of the output y
- Then process just that chunk and append the result to y
In order to make this more efficient, think about what can be pre-computed beforehand and what has to be computed in real-time


In order to make this more efficient, think about what can be pre-computed beforehand and what has to be computed in real-time
- E.g. you have access to the whole recording beforehand, but you don’t know the desired TSM factor that will be adjusted in real-time (though at this stage we will assume that it is constant)
- So you could, for example, pre-compute the STFT beforehand
- We may also want to consider approximations that will greatly speed up the runtime efficiency
    - e.g. you could pre-compute the STFT and instantaneous frequencies beforehand for the whole recording; at runtime the exact current sample location may not match exactly with the offset of the pre-computed STFT (since the analysis hop size will vary depending on the current TSM factor) but it could be a close enough approximation to just find the nearest neighbor and use its pre-computed instantaneous frequency values.  This approach will not be exactly the same as an offline implementation, but it could be much faster at runtime since a lot of the work could be pre-computed beforehand.  Let’s be open to trying such approximations and comparing the quality of the generated time domain signals.
- Once you implement a simulated real-time version of this, you can compare the output to the hw10 offline implementations – they should match either exactly or very close (they should be indistinguishable to the human ear)
    - Have demos of the hw10 offline implementations and your simulated real-time implementation to verify that they match in behavior
- Find most commonly used packages for real-time audio processing
    - Present pros/cons of different options
    - Select what you think is the best option and justify your choice
    - Show code example(s) of real-time audio processing with that package


In [37]:
def tsm_ola_simRealTime(x, sr, alpha):
    




    return None

In [38]:
def tsm_phaseVocoder_simRealTime(x, sr, alpha):





    return None

In [39]:
def tsm_hybrid_simRealTime(x, sr, alpha):




    return None

### Attempt to change volume in real-time:

In [40]:
import tkinter as tk
import pygame
import tkinter.filedialog as filedialog
import soundfile as sf

pygame 2.6.1 (SDL 2.28.4, Python 3.12.5)
Hello from the pygame community. https://www.pygame.org/contribute.html


In [41]:
count = 0
for block in sf.blocks('choir.wav', blocksize=1024):
    count += 1
print(count)

259


In [42]:
len(choir) // 1024

258

In [43]:
# def set_volume(value):
#     """Sets the volume of the music player."""
#     volume = float(value) / 100  # Scale volume to be between 0 and 1
#     pygame.mixer.music.set_volume(volume)

# def play_music(file):
#     """Initializes the music player and starts playing the music."""
#     pygame.mixer.init()
#     pygame.mixer.music.load(file)  # Replace with your song file
#     pygame.mixer.music.play()


# def upload_file(event=None):
#     filename = filedialog.askopenfilename()
#     play_music(filename)

# # Initialize main window
# root = tk.Tk()
# root.title("Music Volume Control")

# button = tk.Button(root, text='Open & Play', command=upload_file)
# button.pack()

# # Create volume slider
# volume_slider = tk.Scale(root, from_=0, to=100, orient=tk.HORIZONTAL, label="Volume", command=set_volume)
# volume_slider.set(100)  # Set initial volume to 100%
# volume_slider.pack()

# root.mainloop()

### Attempting to change alpha in real-time

In [44]:
import wave
import sys
import pyaudio
import soundfile as sf
import io
import keyboard

In [45]:
len(beatbox)//1024

215

In [46]:
a = 10
a.to_bytes()

b'\n'